In [1]:
import sys
sys.path.append("../../../h2o-py/build/main")

In [2]:
import pandas as pd
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score

In [3]:
import h2o
from h2o.estimators import H2ODecisionTreeEstimator
from h2o.estimators import H2OGradientBoostingEstimator
from h2o.estimators import H2ORandomForestEstimator
from h2o.grid.grid_search import H2OGridSearch
h2o.init()

versionFromGradle='3.46.0',projectVersion='3.46.0.99999',branch='valenad-test-test',lastCommitHash='d7daf66d53941dbd75639a0ec6ffe1b2910de62a',gitDescribe='jenkins-3.46.0.2-1-gd7daf66d53',compiledOn='2024-05-24 14:11:07',compiledBy='potte'
Checking whether there is an H2O instance running at http://localhost:54321. connected.


--------------------------  -----------------------------
H2O_cluster_uptime:         23 hours 52 mins
H2O_cluster_timezone:       Europe/Prague
H2O_data_parsing_timezone:  UTC
H2O_cluster_version:        3.46.0.99999
H2O_cluster_version_age:    5 days
H2O_cluster_name:           potte
H2O_cluster_total_nodes:    1
H2O_cluster_free_memory:    10.75 Gb
H2O_cluster_total_cores:    12
H2O_cluster_allowed_cores:  12
H2O_cluster_status:         locked, healthy
H2O_connection_url:         http://localhost:54321
H2O_connection_proxy:       {"http": null, "https": null}
H2O_internal_security:      False
Python_version:             3.9.6 final
--------------------------  -----------------------------

In [4]:
titanic = h2o.import_file('train-prep.csv')

Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%


In [5]:
titanic_train = h2o.import_file('train-split.csv')
titanic_valid = h2o.import_file('valid-split.csv')
target_variable = 'Survived'
train_variables =['Age','Sex','Pclass']

Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%


In [6]:
valid = titanic_valid
train = titanic_train

In [7]:
titanic_valid[titanic_valid['Survived'] == '0'].shape

(0, 11)

In [8]:
titanic_valid[titanic_valid['Survived'] == '1'].shape

(0, 11)

In [9]:
train

PassengerId    Survived    Pclass  Name                                                 Sex       Age    SibSp    Parch    Ticket     Fare  Embarked
-------------  ----------  --------  ---------------------------------------------------  ------  -----  -------  -------  --------  -------  ----------
            1           0         3  Braund, Mr. Owen Harris                              male       22        1        0       nan   7.25    S
            2           1         1  Cumings, Mrs. John Bradley (Florence Briggs Thayer)  female     38        1        0       nan  71.2833  C
            3           1         3  Heikkinen, Miss. Laina                               female     26        0        0       nan   7.925   S
            4           1         1  Futrelle, Mrs. Jacques Heath (Lily May Peel)         female     35        1        0    113803  53.1     S
            5           0         3  Allen, Mr. William Henry                             male       35        0        0    373450   8.05    S
            7           0         1  McCarthy, Mr. Timothy J                              male       54        0        0     17463  51.8625  S
            8           0         3  Palsson, Master. Gosta Leonard                       male        2        3        1    349909  21.075   S
           12           1         1  Bonnell, Miss. Elizabeth                             female     58        0        0    113783  26.55    S
           13           0         3  Saundercock, Mr. William Henry                       male       20        0        0       nan   8.05    S
           14           0         3  Andersson, Mr. Anders Johan                          male       39        1        5    347082  31.275   S
[513 rows x 11 columns]

In [10]:
train[train["Survived"] == '0'].shape

(0, 11)

In [11]:
train[train["Survived"] == '1'].shape

(0, 11)

In [12]:
valid

PassengerId    Survived    Pclass  Name                                               Sex       Age    SibSp    Parch            Ticket     Fare  Embarked
-------------  ----------  --------  -------------------------------------------------  ------  -----  -------  -------  ----------------  -------  ----------
            9           1         3  Johnson, Mrs. Oscar W (Elisabeth Vilhelmina Berg)  female     27        0        2  347742            11.1333  S
           10           1         2  Nasser, Mrs. Nicholas (Adele Achem)                female     14        1        0  237736            30.0708  C
           11           1         3  Sandstrom, Miss. Marguerite Rut                    female      4        1        1     nan            16.7     S
           22           1         2  Beesley, Mr. Lawrence                              male       34        0        0  248698            13       S
           38           0         3  Cann, Mr. Ernest Charles                           male       21        0        0     nan             8.05    S
           44           1         2  Laroche, Miss. Simonne Marie Anne Andree           female      3        1        2     nan            41.5792  C
           50           0         3  Arnold-Franchi, Mrs. Josef (Josefine Franchi)      female     18        1        0  349237            17.8     S
           68           0         3  Crease, Mr. Ernest James                           male       19        0        0     nan             8.1583  S
           69           1         3  Andersson, Miss. Erna Alexandra                    female     17        4        2       3.10128e+06   7.925   S
           71           0         2  Jenkin, Mr. Stephen Curnow                         male       32        0        0     nan            10.5     S
[199 rows x 11 columns]

In [13]:
def make_categorical(dataset):
    dataset[target_variable] = dataset[target_variable].asfactor()
    dataset["Sex"] = dataset["Sex"].asfactor()

In [14]:
make_categorical(train)
make_categorical(valid)

In [15]:
sdt_h2o = H2ODecisionTreeEstimator(model_id="decision_tree.hex", max_depth=5,seed =15468)
sdt_h2o.train(y=target_variable,x = train_variables,training_frame=train)

dt Model Build progress: |███████████████████████████████████████████████████████| (done) 100%


Model Details
=============
H2ODecisionTreeEstimator : Decision Tree
Model Key: decision_tree.hex

No summary for this model

[tips]
Use `model.explain()` to inspect the model.
--
Use `h2o.display.toggle_user_tips()` to switch on/off this section.

In [16]:
predictions = sdt_h2o.predict(valid)
predictions

dt prediction progress: |████████████████████████████████████████████████████████| (done) 100%


predict         p0        p1
---------  ---------  --------
        0  0.571429   0.428571
        1  0.0943396  0.90566
        0  0.571429   0.428571
        0  1          0
        0  0.852941   0.147059
        1  0.0943396  0.90566
        0  0.571429   0.428571
        0  0.852941   0.147059
        0  0.571429   0.428571
        0  0.974359   0.025641
[199 rows x 3 columns]

In [17]:
make_categorical(titanic)

# Grid search for drf

In [18]:
drf_params = {'ntrees' : [10,50,100],
                'max_depth': [3, 5, 9,15,20],
                'sample_rate': [0.8, 1.0],
                'min_rows' : [1.0,5.0,10.0,15.0],
                'col_sample_rate_per_tree': [0.2, 0.5, 1.0]}

In [19]:
drf_gridtitanic = H2OGridSearch(model=H2ORandomForestEstimator,grid_id='drf_gridtitanic',hyper_params=drf_params)

drf_gridtitanic.train(x=train_variables, y=target_variable,training_frame=train,validation_frame=valid,seed=91)

drf Grid Build progress: |███████████████████████████████████████████████████████| (done) 100%


Hyper-Parameter Search Summary: ordered by increasing logloss
     col_sample_rate_per_tree    max_depth    ntrees    sample_rate    model_ids                   logloss
---  --------------------------  -----------  --------  -------------  --------------------------  -------------------
     1.0                         9.0          10.0      0.8            drf_gridtitanic_model_1344  0.4478410500799744
     1.0                         15.0         10.0      0.8            drf_gridtitanic_model_1347  0.4478410500799744
     1.0                         20.0         10.0      0.8            drf_gridtitanic_model_1350  0.4478410500799744
     1.0                         9.0          10.0      0.8            drf_gridtitanic_model_864   0.4478410500799744
     1.0                         15.0         10.0      0.8            drf_gridtitanic_model_867   0.4478410500799744
     1.0                         20.0         10.0      0.8            drf_gridtitanic_model_870   0.4478410500799744
     1.0                         5.0          10.0      0.8            drf_gridtitanic_model_1341  0.45179789906627227
     1.0                         5.0          10.0      0.8            drf_gridtitanic_model_861   0.45179789906627227
     1.0                         15.0         50.0      1.0            drf_gridtitanic_model_1947  0.45193677220310874
     1.0                         20.0         50.0      1.0            drf_gridtitanic_model_1950  0.45193677220310874
---  ---                         ---          ---       ---            ---                         ---
     0.2                         20.0         10.0      1.0            drf_gridtitanic_model_2233  0.5987221549245837
     0.5                         20.0         10.0      1.0            drf_gridtitanic_model_2234  0.5987221549245837
     0.2                         15.0         10.0      0.8            drf_gridtitanic_model_1690  0.6019712757326249
     0.5                         15.0         10.0      0.8            drf_gridtitanic_model_1691  0.6019712757326249
     0.2                         20.0         10.0      0.8            drf_gridtitanic_model_1693  0.6019712757326249
     0.5                         20.0         10.0      0.8            drf_gridtitanic_model_1694  0.6019712757326249
     0.2                         15.0         10.0      0.8            drf_gridtitanic_model_2050  0.6019712757326249
     0.5                         15.0         10.0      0.8            drf_gridtitanic_model_2051  0.6019712757326249
     0.2                         20.0         10.0      0.8            drf_gridtitanic_model_2053  0.6019712757326249
     0.5                         20.0         10.0      0.8            drf_gridtitanic_model_2054  0.6019712757326249
[2760 rows x 7 columns]

In [20]:
drf_gridperf = drf_gridtitanic.get_grid(sort_by='auc', decreasing=True)
drf_gridperf

Hyper-Parameter Search Summary: ordered by decreasing auc
     col_sample_rate_per_tree    max_depth    ntrees    sample_rate    model_ids                   auc
---  --------------------------  -----------  --------  -------------  --------------------------  ------------------
     1.0                         5.0          10.0      1.0            drf_gridtitanic_model_2586  0.854857202418178
     1.0                         15.0         10.0      1.0            drf_gridtitanic_model_2622  0.8535021888680425
     1.0                         20.0         10.0      1.0            drf_gridtitanic_model_2625  0.8535021888680425
     1.0                         9.0          10.0      1.0            drf_gridtitanic_model_1884  0.8523882113821138
     1.0                         9.0          10.0      1.0            drf_gridtitanic_model_2244  0.8523882113821138
     1.0                         15.0         10.0      1.0            drf_gridtitanic_model_1887  0.8516260162601627
     1.0                         20.0         10.0      1.0            drf_gridtitanic_model_1890  0.8516260162601627
     1.0                         15.0         10.0      1.0            drf_gridtitanic_model_2247  0.8516260162601627
     1.0                         20.0         10.0      1.0            drf_gridtitanic_model_2250  0.8516260162601627
     1.0                         9.0          10.0      0.8            drf_gridtitanic_model_2424  0.8510006253908693
---  ---                         ---          ---       ---            ---                         ---
     0.2                         20.0         10.0      1.0            drf_gridtitanic_model_2233  0.7528963414634147
     0.5                         20.0         10.0      1.0            drf_gridtitanic_model_2234  0.7528963414634147
     0.2                         15.0         10.0      0.8            drf_gridtitanic_model_1690  0.7460365853658537
     0.5                         15.0         10.0      0.8            drf_gridtitanic_model_1691  0.7460365853658537
     0.2                         20.0         10.0      0.8            drf_gridtitanic_model_1693  0.7460365853658537
     0.5                         20.0         10.0      0.8            drf_gridtitanic_model_1694  0.7460365853658537
     0.2                         15.0         10.0      0.8            drf_gridtitanic_model_2050  0.7460365853658537
     0.5                         15.0         10.0      0.8            drf_gridtitanic_model_2051  0.7460365853658537
     0.2                         20.0         10.0      0.8            drf_gridtitanic_model_2053  0.7460365853658537
     0.5                         20.0         10.0      0.8            drf_gridtitanic_model_2054  0.7460365853658537
[2760 rows x 7 columns]

In [21]:
best_drf = drf_gridperf.models[0]
best_drf

Model Details
=============
H2ORandomForestEstimator : Distributed Random Forest
Model Key: drf_gridtitanic_model_2586


Model Summary: 
    number_of_trees    number_of_internal_trees    model_size_in_bytes    min_depth    max_depth    mean_depth    min_leaves    max_leaves    mean_leaves
--  -----------------  --------------------------  ---------------------  -----------  -----------  ------------  ------------  ------------  -------------
    10                 10                          2307                   5            5            5             7             17            13.9

ModelMetricsBinomial: drf
** Reported on train data. **

MSE: NaN
RMSE: NaN
LogLoss: NaN
Mean Per-Class Error: NaN
AUC: NaN
AUCPR: NaN
Gini: NaN

ModelMetricsBinomial: drf
** Reported on validation data. **

MSE: 0.1430088351898083
RMSE: 0.37816508986130426
LogLoss: 0.45365305173864334
Mean Per-Class Error: 0.18297894517406715
AUC: 0.854857202418178
AUCPR: 0.844137940504173
Gini: 0.709714404836356

Confusion Matrix (Act/Pred) for max f1 @ threshold = 0.4430542379617691
       0    1    Error    Rate
-----  ---  ---  -------  ------------
0      107  10   0.0855   (10.0/117.0)
1      23   59   0.2805   (23.0/82.0)
Total  130  69   0.1658   (33.0/199.0)

Maximum Metrics: Maximum metrics at their respective thresholds
metric                       threshold    value     idx
---------------------------  -----------  --------  -----
max f1                       0.443054     0.781457  20
max f2                       0.151806     0.793814  34
max f0point5                 0.443054     0.824022  20
max accuracy                 0.443054     0.834171  20
max precision                1            1         0
max recall                   0.0673582    1         40
max specificity              1            1         0
max absolute_mcc             0.443054     0.655725  20
max min_per_class_accuracy   0.323939     0.780488  27
max mean_per_class_accuracy  0.443054     0.817021  20
max tns                      1            117       0
max fns                      1            81        0
max fps                      0.0395381    117       41
max tps                      0.0673582    82        40
max tnr                      1            1         0
max fnr                      1            0.987805  0
max fpr                      0.0395381    1         41
max tpr                      0.0673582    1         40

Gains/Lift Table: Avg response rate: 41,21 %, avg score: 37,77 %
group    cumulative_data_fraction    lower_threshold    lift      cumulative_lift    response_rate    score      cumulative_response_rate    cumulative_score    capture_rate    cumulative_capture_rate    gain      cumulative_gain    kolmogorov_smirnov
-------  --------------------------  -----------------  --------  -----------------  ---------------  ---------  --------------------------  ------------------  --------------  -------------------------  --------  -----------------  --------------------
1        0.0150754                   0.958707           2.42683   2.42683            1                0.972472   1                           0.972472            0.0365854       0.0365854                  142.683   142.683            0.0365854
2        0.0502513                   0.913364           2.42683   2.42683            1                0.913364   1                           0.931096            0.0853659       0.121951                   142.683   142.683            0.121951
3        0.0502513                   0.905163           0         2.42683            0                0          1                           0.931096            0               0.121951                   -100      142.683            0.121951
4        0.115578                    0.882173           2.24015   2.32131            0.923077         0.887375   0.956522                    0.906384            0.146341        0.268293                   124.015   132.131            0.259746
5        0.160804                    0.84

In [22]:
#titanic_drf = H2ORandomForestEstimator(ntrees=100,max_depth=5,min_rows=10,calibrate_model=True,calibration_frame=valid,
#                                   binomial_double_trees=True,seed = 15624)
#titanic_drf.train(x=train_variables,y=target_variable,training_frame=train,validation_frame=valid)

In [23]:
predicts = best_drf.predict(valid)
predicts

drf prediction progress: |███████████████████████████████████████████████████████| (done) 100%


predict         p0        p1
---------  ---------  --------
        1  0.556946   0.443054
        1  0.164653   0.835347
        1  0.304359   0.695641
        0  0.863748   0.136252
        0  0.848194   0.151806
        1  0.0412926  0.958707
        1  0.556946   0.443054
        0  0.848194   0.151806
        1  0.556946   0.443054
        0  0.863748   0.136252
[199 rows x 3 columns]

In [24]:
drf_gridtitanic.model_performance(valid = True)

{'drf_gridtitanic_model_1344': ModelMetricsBinomial: drf
** Reported on validation data. **

MSE: 0.14512301114032075
RMSE: 0.3809501425912855
LogLoss: 0.4478410500799744
Mean Per-Class Error: 0.21442133815551537
AUC: 0.8478300180831826
AUCPR: 0.805173519287872
Gini: 0.6956600361663652

Confusion Matrix (Act/Pred) for max f1 @ threshold = 0.30417402982711794
       0    1    Error    Rate
-----  ---  ---  -------  ------------
0      103  37   0.2643   (37.0/140.0)
1      13   66   0.1646   (13.0/79.0)
Total  116  103  0.2283   (50.0/219.0)

Maximum Metrics: Maximum metrics at their respective thresholds
metric                       threshold    value     idx
---------------------------  -----------  --------  -----
max f1                       0.304174     0.725275  38
max f2                       0.304174     0.787589  38
max f0point5                 0.778278     0.810811  18
max accuracy                 0.696719     0.821918  22
max precision                0.965029     1         0


# Grid search for gbm

In [25]:
gbm_params1 = {'learn_rate': [0.01, 0.1,0.3,1.0],
               'ntrees' : [10,50,100],
                'max_depth': [3, 5, 9,15,20],
                'sample_rate': [0.8, 1.0],
               'min_rows' : [1.0,5.0,10.0,15.0],
                'col_sample_rate': [0.2, 0.5, 1.0]}

In [26]:
gbm_gridtitanic = H2OGridSearch(model=H2OGradientBoostingEstimator,grid_id='gbm_gridtitanic',hyper_params=gbm_params1)

gbm_gridtitanic.train(x=train_variables, y=target_variable,training_frame=train,validation_frame=valid,seed=51)

gbm Grid Build progress: |███████████████████████████████████████████████████████| (done) 100%


H2OConnectionError: Unexpected HTTP error: HTTPConnectionPool(host='localhost', port=54321): Max retries exceeded with url: /3/Models/gbm_gridtitanic_model_12204 (Caused by NewConnectionError('<urllib3.connection.HTTPConnection object at 0x00000234F553C9D0>: Failed to establish a new connection: [WinError 10061] Nemohlo být vytvořeno žádné připojení, protože cílový počítač je aktivně odmítl'))

In [ ]:
gbm_gridperf1 = gbm_gridtitanic.get_grid(sort_by='auc', decreasing=True)
gbm_gridperf1

In [ ]:
best_gbm1 = gbm_gridperf1.models[0]
best_gbm1

In [ ]:
#titanic_gbm = H2OGradientBoostingEstimator(nfolds=5,seed=1111,keep_cross_validation_predictions = True)
#titanic_gbm.train(x=train_variables,y=target_variable, training_frame=titanic)

In [ ]:
predict = best_gbm1.predict(valid)
predict

In [ ]:
valid = valid.as_data_frame()

In [ ]:
predicts = predicts['predict'].as_data_frame()

In [ ]:
predict = predict['predict'].as_data_frame()

In [ ]:
valid = valid['Survived'] 

In [ ]:
score=accuracy_score(valid, predict)
score

In [ ]:
score=accuracy_score(valid, predicts)
score

In [ ]:
#h2o.cluster().shutdown()